In [23]:
import pandas as pd
import numpy as np
import requests
from nba_api.stats import endpoints
from nba_api.stats.endpoints import playergamelog

In [24]:
def de_que_equipo_es(valor_buscar,dict_equipo_jugador):
    for equipo, jugadores in dict_equipo_jugador.items():
        if valor_buscar in jugadores:
            return equipo
    else:
        print(f"No se encontró")


In [25]:
def get_player_season(player_id, season):
    # Obtener los registros de juegos del jugador para la temporada especificada
    games_data = playergamelog.PlayerGameLog(player_id=player_id, season=season)
    games = games_data.get_data_frames()[0]
    
    
    # Filtrar solo las columnas relevantes para calcular el PER
    relevant_columns = ['Game_ID', 'GAME_DATE', 'WL','PTS', 'REB','OREB', 'DREB', 'AST',
                        'STL', 'BLK', 'TOV', 'PF', 'MIN', 'FGM', 'FGA', 'FG3M', 'FG3A',  
                        'FTM', 'FTA', 'PLUS_MINUS']
    games_filtered = games[relevant_columns]
    
    # Calcular el PER (Player Efficiency Rating)
    '''
    games_filtered.loc[:, 'PER'] = (games_filtered['PTS'] + games_filtered['REB'] + games_filtered['AST'] +
                                games_filtered['STL'] + games_filtered['BLK'] - games_filtered['TOV'] -
                                games_filtered['PF']) / games_filtered['MIN']
    '''
    
    return games_filtered

In [32]:
def sacar_df(player_id,season,dict_equipo_jugador):
    player_per_stats = get_player_season(player_id, season)
    player_per_stats['GAME_DATE'] = pd.to_datetime(player_per_stats['GAME_DATE'], format='%b %d, %Y')
    player_per_stats = player_per_stats.sort_values(by='GAME_DATE')

    # Restablecer los índices del DataFrame
    player_per_stats.reset_index(drop=True, inplace=True)

    # Imprimir las primeras 5 filas del DataFrame ordenado
    # Suponiendo que ya tienes el DataFrame df_sorted ordenado por fecha
    # Eliminar las primeras 10 filas
    player_per_stats['WL'] = player_per_stats['WL'].replace({'W': 1, 'L': 0})
    # Calcular el promedio del PER de los últimos 10 partidos para cada juego
    col=['WL', 'MIN', 'FGM', 'FGA', 'FG3M', 'FG3A',  'FTM', 'FTA','OREB', 'DREB', 'AST', 'STL', 'BLK', 'TOV', 'PF','PTS', 'PLUS_MINUS']
    promedio_ultimos_10 = player_per_stats[col].shift(1).rolling(window=10, min_periods=1).mean()
    player_per_stats.update(promedio_ultimos_10)
    player_per_stats['PLAYER_ID']=player_id
    player_per_stats=player_per_stats[1:]
    player_per_stats['TEAM_ID'] = player_per_stats['PLAYER_ID'].apply(lambda x: de_que_equipo_es(x, dict_equipo_jugador))
    player_per_stats.drop(columns=['GAME_DATE'], inplace=True)
    
    return player_per_stats
   


In [33]:
#data = endpoints.leagueleaders.LeagueLeaders() 
temporadas = ['2023-24']
dfs = []

# Iterar sobre cada temporada y obtener las estadísticas de los líderes de la liga
for temporada in temporadas:
    data = endpoints.leagueleaders.LeagueLeaders(season=temporada)
    df = data.league_leaders.get_data_frame()
    # Agregar columna de temporada
    df['Temporada'] = temporada
    dfs.append(df)

# Concatenar todos los DataFrames en uno solo
result = pd.concat(dfs, ignore_index=True)

# Guardar el DataFrame combinado en un archivo CSV
result.to_csv('all_players_stats.csv', index=False)

In [28]:
dict_equipo_jugador = result.groupby('TEAM_ID')['PLAYER_ID'].apply(list).to_dict()

l_player_id = result['PLAYER_ID'].tolist()
season = '2023-24'

In [34]:

# Inicializar un DataFrame vacío
df_concatenado = pd.DataFrame()

# Iterar sobre cada player_id en l_player_id
for player_id in l_player_id:
    # Generar el DataFrame para el jugador actual
    df_actual = sacar_df(player_id, season, dict_equipo_jugador)
    
    # Concatenar el DataFrame actual con el DataFrame concatenado
    df_concatenado = pd.concat([df_concatenado, df_actual], ignore_index=True)

# Mostrar el DataFrame concatenado
df_concatenado

    

C:\Users\ce200\AppData\Local\Temp\ipykernel_6924\814845403.py:12: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  player_per_stats['WL'] = player_per_stats['WL'].replace({'W': 1, 'L': 0})
C:\Users\ce200\AppData\Local\Temp\ipykernel_6924\814845403.py:16: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value '[1.         1.         1.         1.         1.         0.8
 0.83333333 0.85714286 0.75       0.77777778 0.8        0.7
 0.7        0.6        0.5        0.6        0.5        0.5
 0.5        0.5        0.5        0.6        0.6        0.6
 0.7        0.6        0.6        0.6        0.7        0.6
 0.6        0.5        0.5        0.6        0.5        0.5
 0.5        0.4        0.4        0.4 

Game_ID   WL    PTS  REB      OREB  DREB        AST   STL       BLK  \
0      0022300084  1.0  33.00   10  1.000000  12.0  10.000000  2.00  0.000000   
1      0022300106  1.0  41.00   12  1.000000  10.5   8.500000  1.00  0.000000   
2      0022300124  1.0  39.00    7  0.666667  11.0   9.666667  1.00  0.333333   
3      0022300006  1.0  33.75   10  0.500000  10.0   9.750000  1.25  0.500000   
4      0022300143  0.8  33.80   12  1.000000   9.4   9.400000  1.00  0.600000   
...           ...  ...    ...  ...       ...   ...        ...   ...       ...   
25824  0022300596  0.6   0.00    1  0.000000   0.4   0.300000  0.10  0.000000   
25825  0022300631  0.7   0.00    0  0.000000   0.4   0.300000  0.00  0.000000   
25826  0022300643  0.7   0.00    0  0.000000   0.3   0.200000  0.10  0.000000   
25827  0022300657  0.8   0.00    1  0.000000   0.3   0.200000  0.10  0.000000   
25828  0022300671  0.8   0.00    0  0.000000   0.3   0.100000  0.10  0.000000   

            TOV  ...        MIN        FGM   FGA  FG3M       FG3A       FTM  \
0      4.000000  ...  34.000000  13.000000  25.0  3.00  11.000000  4.000000   
1      2.000000  ...  35.000000  14.500000  25.0  6.00  12.500000  6.000000   
2      3.333333  ...  36.666667  13.333333  24.0  6.00  12.333333  6.333333   
3      4.000000  ...  37.500000  11.250000  22.0  4.75  11.250000  6.500000   
4      5.000000  ...  37.600000  11.200000  22.4  5.00  11.200000  6.400000   
...         ...  ...        ...        ...   ...   ...        ...       ...   
25824  0.000000  ...   2.200000   0.000000   0.4  0.00   0.400000  0.000000   
25825  0.000000  ...   2.300000   0.000000   0.4  0.00   0.400000  0.000000   
25826  0.000000  ...   2.700000   0.000000   0.5  0.00   0.500000  0.000000   
25827  0.100000  ...   2.500000   0.000000   0.4  0.00   0.400000  0.000000   
25828  0.100000  ...   2.500000   0.000000   0.3  0.00   0.300000  0.000000   

       FTA  PLUS_MINUS  PLAYER_ID     TEAM_ID  
0      7.0    4.000000    1629029  1610612742  
1      8.5    6.500000    1629029  1610612742  
2      9.0    6.333333    1629029  1610612742  
3      9.0    7.500000    1629029  1610612742  
4      8.6    5.200000    1629029  1610612742  
...    ...         ...        ...         ...  
25824  0.0    0.100000    1627853  1610612752  
25825  0.0    0.800000    1627853  1610612752  
25826  0.0    1.200000    1627853  1610612752  
25827  0.0   -0.200000    1627853  1610612752  
25828  0.0    0.300000    1627853  1610612752  

[25829 rows x 21 columns]

In [36]:
df_concatenado.to_csv('df_players_finales.csv')